## NBA Model TEST 1

In [20]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import shap
import os
import pickle

import warnings
warnings.filterwarnings('ignore')

from sklearn.linear_model import LinearRegression
from sklearn.svm import SVR
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import ElasticNet
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import AdaBoostRegressor
from sklearn.ensemble import GradientBoostingRegressor
from lightgbm import LGBMRegressor

from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error, r2_score

In [21]:
# Defining the seasons and models used
# seasons = ['1999_2000', '2000_2001', '2001_2002', '2002_2003', '2003_2004', '2004_2005', '2005_2006', 
#           '2006_2007', '2007_2008', '2008_2009',  '2009_2010', '2010_2011', '2011_2012', '2012_2013', 
#           '2013_2014', '2014_2015', '2015_2016', '2016_2017', '2017_2018', '2018_2019', '2019_2020',   
#           '2020_2021', '2021_2022', '2022_2023'] 
seasons = ['2021_2022', '2001_2002', '2002_2003', '2003_2004', '2004_2005', '2005_2006', 
          '2006_2007', '2007_2008', '2008_2009',  '2009_2010', '2010_2011', '2011_2012', '2012_2013', 
          '2013_2014', '2014_2015', '2015_2016', '2016_2017', '2017_2018', '2018_2019', '2019_2020',   
          '2020_2021']
modelos = ['SVM','Elastic Net','Random Forest','AdaBoost','Gradient Boosting','LGBM']

# Path to local folder
path_data = r'/Users/lilgl/Downloads/BrainStation_Final_Project/'

# sep = r'/'

In [22]:
def get_data(seasons):
# Opening the data
    perGame = pd.DataFrame()
    totals = pd.DataFrame()
    advanced = pd.DataFrame()
    standings = pd.DataFrame()
    
    for season in seasons:

        _advanced = pd.read_csv(path_data + "nba" + season + " Advanced.csv")
        
        _perGame = pd.read_csv(path_data + "nba" + season + " perGame.csv")

        _standings = pd.read_csv(path_data + "nba" + season + " Standings.csv")
        
        _totals = pd.read_csv(path_data + "nba" + season + " Totals.csv")
        

        _perGame['Season'] = season
        _totals['Season'] = season
        _advanced['Season'] = season
        _standings['Season'] = season
        
        perGame = pd.concat([perGame,_perGame], ignore_index=True)
        totals = pd.concat([totals,_totals], ignore_index=True)
        advanced = pd.concat([advanced,_advanced], ignore_index=True)
        standings = pd.concat([standings,_standings], ignore_index=True)
            
    return advanced, perGame, standings, totals;



In [23]:
# for season in seasons:
#   _standings = pd.read_csv(path_data + "nba" + season + " Standings.csv", skiprows=1)
#   # _standings.drop(index=_standings.index[0], axis=0, inplace=True)
#   df = _standings[['Rk', 'Team', 'Overall']]
#   df.rename(columns={'Rk': 'Seed', 'Overall': 'Record'}, inplace=True)
#   print(df.columns)
#   df.to_csv(path_data + "nba" + season + " Standings.csv", index=False)


In [24]:
def treat_data(advanced, perGame, standings, totals, seasons):
    
    # Removing duplicate/empty columns
    perGame = perGame.drop(['Rk','Pos','Player-additional'], axis=1)
    totals = totals.drop(['Rk','Pos','Age','G','GS','Player-additional'], axis=1)
    advanced = advanced.drop(['Rk','Pos','Age','G','MP','Unnamed: 24','Unnamed: 19', 'Player-additional'], axis=1)
    
    cols = ['Player','Season','Pos','Age','Tm','G','GS']
    
    # Identifying the variables
    for column in perGame.columns:
        if column not in cols:
            newCol = column+'_perGame'
            perGame = perGame.rename(columns={column:newCol})
    for column in totals.columns:
        if column not in cols:
            newCol = column+'_totals'
            totals = totals.rename(columns={column:newCol})
    for column in advanced.columns:
        if column not in cols:
            newCol = column+'_advanced'
            advanced = advanced.rename(columns={column:newCol})
        # Merging the bases
    data = perGame.merge(advanced, on=['Player','Season','Tm'], how='left', validate='1:1')
    data = data.merge(totals, on=['Player','Season','Tm'], how='left', validate='1:1')
    
    dict_teams = {'Utah Jazz':'UTA','Phoenix Suns':'PHO',
                'Philadelphia 76ers':'PHI','Brooklyn Nets':'BRK',
                'Denver Nuggets':'DEN','Los Angeles Clippers':'LAC',
                'Milwaukee Bucks':'MIL','Dallas Mavericks':'DAL',
                'Los Angeles Lakers':'LAL','Portland Trail Blazers':'POR',
                'Atlanta Hawks':'ATL','New York Knicks':'NYK',
                'Miami Heat':'MIA','Golden State Warriors':'GSW',
                'Memphis Grizzlies':'MEM','Boston Celtics':'BOS',
                'Washington Wizards':'WAS','Indiana Pacers':'IND',
                'Charlotte Hornets':'CHO','Charlotte Bobcats':'CHA',
                'San Antonio Spurs':'SAS','Chicago Bulls':'CHI',
                'New Orleans Pelicans':'NOP','Sacramento Kings':'SAC',
                'Toronto Raptors':'TOR','Minnesota Timberwolves':'MIN',
                'Cleveland Cavaliers':'CLE','Oklahoma City Thunder':'OKC',
                'Orlando Magic':'ORL','Detroit Pistons':'DET',
                'Houston Rockets':'HOU','New Jersey Nets':'NJN',
                'New Orleans Hornets':'NOH','Seattle SuperSonics':'SEA'}
    
    teams = pd.DataFrame.from_dict(dict_teams, orient='index').reset_index()
    teams = teams.rename(columns={'index':'Team',0:'Tm'})
    standings = standings.merge(teams, on='Team', how='left', validate='m:1')
    wins = (standings['Record'].str.split('-',expand=True)[0]).astype(int)
    games = ((standings['Record'].str.split('-',expand=True)[0]).astype(int)+(standings['Record'].str.split('-',expand=True)[1]).astype(int))
    standings['WIN%'] = wins/games
    
    data = data.merge(standings, on=['Tm','Season'], how='left', validate='m:1')
    
    data['Player'] = data['Player'].str.replace('*','')
    
    mvps = pd.read_csv(path_data + "MVPs.csv")
    data = data.merge(mvps, on=['Player','Season'], how='left', validate='m:1').fillna(0)  

    data['Player'] = data['Player'].str.split('\\', expand=True)[0]
    
    # Removing duplicate lines from traded players
    dataf = pd.DataFrame()
    for season in seasons:
        data_season = data[data['Season']==season]
        data_season = data_season.drop_duplicates(subset=['Player'], keep='first')

        dataf = pd.concat([dataf,data_season], ignore_index=True)
        
    # Filtering the data
    dataf = dataf[((dataf['G']>48)&(dataf['PTS_perGame']>13.5)&(dataf['MP_perGame']>30)
                &(dataf['Seed']<=16)&(dataf['AST_perGame']>1)&(dataf['TRB_perGame']>3)
                &(dataf['Tm']!='TOT')&(dataf['FG%_perGame']>0.37)&(dataf['FGA_perGame']>10)
                &(dataf['PER_advanced']>18)) | (dataf['MVP Votes Share']>0)].reset_index(drop=True)
    
    # Base for the criteria:
    # Karl Malone was MVP in 98-99 with 49 games
    # Wes Unseld was MVP at 68-69 with 13.8 PPG and with 10.9 FGA
    # Steve Nash was MVP at 04-05 with 3.3 REB
    # Moses Malone was MVP at 82-83 with 1.3 AST
    # Bob Cousy was MVP at 56-57 with 37.8% FG
    # Giannis Antetokounmpo was MVP in 19-20 with 30.4 min
    # Kareem Abdul-Jabbar was the only MVP not to make the playoffs in 1976 (40-42)
    # Dave Cowens was MVP at 72-73 with a PER of 18.1
    # Never has an MVP been traded in the middle of the season that he won the award
        
    dataf = dataf.drop(['Tm','Team','Record'], axis=1)
    
    return dataf

In [25]:
advanced, perGame, standings, totals = get_data(seasons)

In [26]:
data = treat_data(advanced, perGame, standings, totals, seasons)


In [27]:
data

Player  Age   G  GS_x  MP_perGame  FG_perGame  \
0              Bam Adebayo   24  56    56        32.6         7.3   
1    Giannis Antetokounmpo   27  67    67        32.9        10.3   
2             Devin Booker   25  68    68        34.5         9.7   
3             Jaylen Brown   25  66    66        33.6         8.7   
4             Jimmy Butler   32  57    57        33.9         7.0   
..                     ...  ...  ..   ...         ...         ...   
446     Michael Porter Jr.   22  61    54        31.3         7.3   
447          Julius Randle   26  71    71        37.6         8.5   
448            Ben Simmons   24  58    58        32.4         5.6   
449           Jayson Tatum   22  64    64        35.8         9.5   
450             Trae Young   22  63    63        33.7         7.7   

     FGA_perGame  FG%_perGame  3P_perGame  3PA_perGame  ...  AST_totals  \
0           13.0        0.557         0.0          0.1  ...         190   
1           18.6        0.553         1.1          3.6  ...         388   
2           20.9        0.466         2.7          7.0  ...         329   
3           18.4        0.473         2.5          7.0  ...         231   
4           14.5        0.480         0.5          2.0  ...         312   
..           ...          ...         ...          ...  ...         ...   
446         13.4        0.542         2.8          6.3  ...          70   
447         18.6        0.456         2.3          5.5  ...         427   
448         10.1        0.557         0.1          0.2  ...         401   
449         20.6        0.459         2.9          7.6  ...         276   
450         17.7        0.438         2.2          6.3  ...         594   

     STL_totals  BLK_totals  TOV_totals  PF_totals  PTS_totals  Seed  \
0            80          44         148        171        1068   4.0   
1            72          91         219        212        2002   7.0   
2            77          26         162        180        1822   1.0   
3            70          18         178        163        1559   6.0   
4            94          27         121         88        1219   4.0   
..          ...         ...         ...        ...         ...   ...   
446          40          54          77        126        1162   5.0   
447          64          18         241        225        1712  12.0   
448          93          35         173        171         829   3.0   
449          75          31         171        122        1692  16.0   
450          53          12         261        111        1594  11.0   

         WIN%  MVP Rank  MVP Votes Share  
0    0.646341         0              0.0  
1    0.621951         0              0.0  
2    0.780488         0              0.0  
3    0.621951         0              0.0  
4    0.646341         0              0.0  
..        ...       ...              ...  
446  0.652778         0              0.0  
447  0.569444         0              0.0  
448  0.680556         0              0.0  
449  0.500000         0              0.0  
450  0.569444         0              0.0  

[451 rows x 98 columns]

In [28]:
data.columns # Variables


Index(['Player', 'Age', 'G', 'GS_x', 'MP_perGame', 'FG_perGame', 'FGA_perGame',
       'FG%_perGame', '3P_perGame', '3PA_perGame', '3P%_perGame', '2P_perGame',
       '2PA_perGame', '2P%_perGame', 'eFG%_perGame', 'FT_perGame',
       'FTA_perGame', 'FT%_perGame', 'ORB_perGame', 'DRB_perGame',
       'TRB_perGame', 'AST_perGame', 'STL_perGame', 'BLK_perGame',
       'TOV_perGame', 'PF_perGame', 'PTS_perGame', 'Season', 'PER_advanced',
       'TS%_advanced', '3PAr_advanced', 'FTr_advanced', 'ORB%_advanced',
       'DRB%_advanced', 'TRB%_advanced', 'AST%_advanced', 'STL%_advanced',
       'BLK%_advanced', 'TOV%_advanced', 'USG%_advanced', 'OWS_advanced',
       'DWS_advanced', 'WS_advanced', 'WS/48_advanced', 'OBPM_advanced',
       'DBPM_advanced', 'BPM_advanced', 'VORP_advanced', 'GS_y', 'FG_advanced',
       'FGA_advanced', 'FG%_advanced', '3P_advanced', '3PA_advanced',
       '3P%_advanced', '2P_advanced', '2PA_advanced', '2P%_advanced',
       'eFG%_advanced', 'FT_advanced', 'FTA_adv

In [29]:
data['Season'].value_counts() # Number of players in the data per season


2016_2017    27
2007_2008    27
2010_2011    26
2006_2007    26
2005_2006    24
2021_2022    24
2003_2004    23
2009_2010    23
2011_2012    23
2018_2019    23
2020_2021    23
2001_2002    22
2013_2014    21
2014_2015    21
2012_2013    20
2002_2003    20
2017_2018    20
2019_2020    20
2004_2005    19
2008_2009    19
Name: Season, dtype: int64

In [30]:
# Function for metrics
def func_metricas(y_test, y_pred, metrics, model, season):
    rmse = round(np.sqrt(mean_squared_error(y_test, y_pred)),3) # RMSE
    r2 = round(r2_score(y_test, y_pred),3) # R²
    
    dict_met = {'Modelo': [model],
                'Season': [season],
                'RMSE': [rmse],
                'R²': [r2]}
    
    metrica = pd.DataFrame(data=dict_met)
    metrics = pd.concat([metrics,metrica])
    
    return metrics

In [31]:
def func_modelos(data, seasons, modelos, n_seasons_to_test):
    final_results = pd.DataFrame()
    metricas = pd.DataFrame()
    best_params = []
    i = 1

    for season in seasons:

        # Separating training and testing bases
        season_teste = season

        data_train = data[data['Season']!=season_teste]
        data_test = data[data['Season']==season_teste]

        X_train = data_train.drop(['MVP Votes Share','MVP Rank','Player','Season'], axis=1)
        y_train = data_train['MVP Votes Share']

        X_test = data_test.drop(['MVP Votes Share','MVP Rank','Player','Season'], axis=1)
        y_test = data_test['MVP Votes Share']

        initial_results = data_test[['Player','Season','MVP Votes Share','MVP Rank']]
        results = initial_results.copy()

        scaler = StandardScaler()

        scaled_X_train = scaler.fit_transform(X_train)
        scaled_X_test = scaler.transform(X_test)

        for modelo in modelos:
            # Creating instance for each model
            if modelo=='SVM':
                param_grid = {'C': [0.001,0.01,0.1,0.5,1,2,5,10],
                             'kernel': ['linear','rbf','poly'],
                             'gamma': ['scale','auto'],
                             'degree': [2,3,4],
                             'epsilon': [0.1,0.5,1]}
                svr_model = SVR()
                grid = GridSearchCV(svr_model, param_grid)
                grid.fit(scaled_X_train, y_train)
                model = SVR(**grid.best_params_)
                best_params.append(grid.best_params_)

            elif modelo=='Elastic Net':
                param_grid = {'alpha':[0.01,0.1,1,5,10,50,100],
                              'l1_ratio':[0.01,0.1,0.5,0.7,0.95,0.99,1]}
                elastic_net_model = ElasticNet()
                grid = GridSearchCV(elastic_net_model, param_grid)
                grid.fit(scaled_X_train, y_train)
                grid.best_params_
                model = ElasticNet(**grid.best_params_)
                best_params.append(grid.best_params_)
                
            elif modelo=='Random Forest':
                param_grid = {'n_estimators': [15,25,50,64,100,150,200],
                             'max_features': [2,3,4,5],
                             'bootstrap': [True,False],
                             'oob_score': [True]}
                rfc = RandomForestRegressor()
                grid = GridSearchCV(rfc, param_grid)
                grid.fit(scaled_X_train, y_train)
                model = RandomForestRegressor(**grid.best_params_)
                best_params.append(grid.best_params_)
                
            elif modelo=='AdaBoost':
                param_grid = {'n_estimators': [5,10,20,30,40,50,100],
                             'learning_rate': [0.01,0.05,0.1,0.2,0.5]}
                ada_model = AdaBoostRegressor()
                grid = GridSearchCV(ada_model, param_grid)
                grid.fit(scaled_X_train, y_train)
                model = AdaBoostRegressor(**grid.best_params_)
                best_params.append(grid.best_params_)
                
            elif modelo=='Gradient Boosting':
                param_grid = {'n_estimators': [10,20,30,40,50],
                             'learning_rate': [0.01,0.05,0.1,0.2,0.5],
                             'max_depth': [3,4,5]}
                gb_model = GradientBoostingRegressor()
                grid = GridSearchCV(gb_model, param_grid)
                grid.fit(scaled_X_train, y_train)
                model = GradientBoostingRegressor(**grid.best_params_)
                best_params.append(grid.best_params_)
                
            elif modelo=='LGBM':
                param_grid = {'learning_rate':[0.01,0.1,0.2,0.3],
                              'num_leaves':[5,10,20,30],
                              'min_data_in_leaf':[10,25,50],
                              'max_depth':[2,3,4],
                              'feature_fraction':[0.6,0.7,0.8,0.9],
                              'min_gain_to_split':[0,0.01,0.1,0.2],
                              'verbose':[-1]}
                lgbm_model = LGBMRegressor()
                grid = GridSearchCV(lgbm_model, param_grid)
                grid.fit(scaled_X_train, y_train)
                model = LGBMRegressor(**grid.best_params_)
                best_params.append(grid.best_params_)
                
            model.fit(scaled_X_train, y_train)
            
            pickle.dump(model, open(path_data +'Modelos'+"/"+ modelo+'.dat', 'wb'))

            
            y_pred = model.predict(scaled_X_test)
            metricas = func_metricas(y_test, y_pred, metricas, modelo, season)

            apoio = initial_results.copy()
            apoio['Predicted MVP Share '+modelo] = pd.Series(y_pred).values

            results_sorted = apoio.sort_values(by='Predicted MVP Share '+modelo,
                                                ascending=False).reset_index(drop=True)
            results_sorted['MVP Rank '+modelo] = results_sorted.index+1

            results = results.merge(results_sorted, on=['Player','Season','MVP Votes Share','MVP Rank'])

        final_results = pd.concat([final_results,results], ignore_index=True)

        if i == n_seasons_to_test:
            break

        i = i + 1
    
    np.savetxt(path_data+ r'Modelos params.csv', best_params, delimiter =', ', fmt ='% s')
    
    return final_results, metricas, best_params

In [32]:
def media_metricas(metricas):
    # Averages of each of the models
    final_metricas = pd.DataFrame()
    for modelo in metricas['Modelo'].unique():
        metrica = metricas[metricas['Modelo']==modelo]
        rmse = round(metrica['RMSE'].mean(),3)
        r2 = round(metrica['R²'].mean(),3)

        dict_met = {'Modelo': [modelo],
                    'RMSE': [rmse],
                    'R²': [r2]}

        apoio = pd.DataFrame(data=dict_met)
        final_metricas = pd.concat([final_metricas,apoio], ignore_index=True)
    return final_metricas

In [33]:
final_results, metricas, best_params = func_modelos(data, seasons, modelos, 1)
final_metricas = media_metricas(metricas)
final_metricas

[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=10, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=10
[LightGBM] [Warning] min_gain_to_split is set=0, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=10, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=10
[LightGBM] [Warning] min_gain_to_split is set=0, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=10, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=10
[LightGBM] [Warning] m

Modelo  RMSE   R²
0                SVM   0.0  1.0
1        Elastic Net   0.0  1.0
2      Random Forest   0.0  1.0
3           AdaBoost   0.0  1.0
4  Gradient Boosting   0.0  1.0
5               LGBM   0.0  1.0

In [34]:
def create_rank(final_results, n_rank):
    rank_final = pd.DataFrame()

    for season in final_results['Season'].unique():
        temp = final_results[final_results['Season']==season]
        rank = pd.DataFrame()
        rank_real = temp.sort_values(by='MVP Votes Share', ascending=False)[:n_rank].reset_index(drop=True)
        rank['MVP Rank Real'] = rank_real['Player']
        rank['MVP Share Real'] = rank_real['MVP Votes Share']
        for modelo in modelos:
            try:
                temp2 = temp.sort_values(by='Predicted MVP Share '+modelo, ascending=False)[:n_rank].reset_index(drop=True)
                rank['MVP Rank '+modelo] = temp2['Player']
                rank['MVP Share '+modelo] = round(temp2['Predicted MVP Share '+modelo],3)
            except:
                continue

        rank['Season'] = season    
        rank_final = pd.concat([rank_final, rank], ignore_index=True)
    
    return rank_final

In [35]:
rank_final = create_rank(final_results, 3)
rank_final

MVP Rank Real  MVP Share Real           MVP Rank SVM  \
0            Bam Adebayo             0.0            Bam Adebayo   
1  Giannis Antetokounmpo             0.0  Giannis Antetokounmpo   
2         Nikola Vučević             0.0         Nikola Vučević   

   MVP Share SVM   MVP Rank Elastic Net  MVP Share Elastic Net  \
0            0.0            Bam Adebayo                    0.0   
1            0.0  Giannis Antetokounmpo                    0.0   
2            0.0         Nikola Vučević                    0.0   

  MVP Rank Random Forest  MVP Share Random Forest      MVP Rank AdaBoost  \
0            Bam Adebayo                      0.0            Bam Adebayo   
1  Giannis Antetokounmpo                      0.0  Giannis Antetokounmpo   
2         Nikola Vučević                      0.0         Nikola Vučević   

   MVP Share AdaBoost MVP Rank Gradient Boosting  MVP Share Gradient Boosting  \
0                 0.0                Bam Adebayo                          0.0   
1                 0.0      Giannis Antetokounmpo                          0.0   
2                 0.0             Nikola Vučević                          0.0   

           MVP Rank LGBM  MVP Share LGBM     Season  
0            Bam Adebayo             0.0  2021_2022  
1  Giannis Antetokounmpo             0.0  2021_2022  
2         Nikola Vučević             0.0  2021_2022

In [36]:
def temporadas_antigas(data, seasons, modelos, n_seasons_to_test):
    final_results = pd.DataFrame()
    metricas = pd.DataFrame()
    best_params = []
    i = 1

    for season in seasons:
            
        # Separating training and testing bases
        season_teste = season

        data_train = data[data['Season']!=season_teste]
        data_test = data[data['Season']==season_teste]

        X_train = data_train.drop(['MVP Votes Share','MVP Rank','Player','Season'], axis=1)
        y_train = data_train['MVP Votes Share']

        X_test = data_test.drop(['MVP Votes Share','MVP Rank','Player','Season'], axis=1)
        y_test = data_test['MVP Votes Share']

        initial_results = data_test[['Player','Season','MVP Votes Share','MVP Rank']]
        results = initial_results.copy()

        scaler = StandardScaler()

        scaled_X_train = scaler.fit_transform(X_train)
        scaled_X_test = scaler.transform(X_test)

        for modelo in modelos:
            
            if modelo=='Elastic Net':
                continue
            
            # Opening the models already created  
            # pickle.dump(model, open(path_data +'Modelos'+"/"+ modelo+'.dat', 'wb'))        
            model = pickle.load(open(path_data +'Modelos'+"/"+ modelo+'.dat', 'rb'))
                
            model.fit(scaled_X_train, y_train)
            y_pred = model.predict(scaled_X_test)
            metricas = func_metricas(y_test, y_pred, metricas, modelo, season)

            apoio = initial_results.copy()
            apoio['Predicted MVP Share '+modelo] = pd.Series(y_pred).values

            results_sorted = apoio.sort_values(by='Predicted MVP Share '+modelo,
                                                ascending=False).reset_index(drop=True)
            results_sorted['MVP Rank '+modelo] = results_sorted.index+1

            results = results.merge(results_sorted, on=['Player','Season','MVP Votes Share','MVP Rank'])

        final_results = pd.concat([final_results,results], ignore_index=True)

        if i == n_seasons_to_test:
            break

        i = i + 1
        
    return final_results, metricas

In [37]:
# final_results, metricas = temporadas_antigas(data, seasons, modelos, 16)
# final_metricas = media_metricas(metricas)
# final_metricas

In [38]:
data_test = data[data['Season']=='2021-22']
X_test = data_test.drop(['MVP Votes Share','MVP Rank','Player','Season'], axis=1)

scaler = StandardScaler()

scaled_X_test = scaler.transform(X_test)

NotFittedError: This StandardScaler instance is not fitted yet. Call 'fit' with appropriate arguments before using this estimator.